In [1]:
import os
from pathlib import Path

In [2]:
str_path = os.getcwd()
str_path

'A:\\Arbeitsaufgaben\\Instandhaltung'

In [5]:
p = Path(str_path)

In [78]:
folder = list((p / 'results' / 'test_new2').glob('*'))

In [79]:
folder

[WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-3_remove_NA.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-5_analyse_feature.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-1_build_cosSim_matrix.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-2_filt_thresh_cosSim_matrix.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step_3_CosSim-FilterCandidates.xlsx'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-3_list_cosSim_dupl_candidates.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Merge_Duplicates_Step-1_merge_similarity_dupl.pkl')]

In [1]:
%load_ext autoreload
%autoreload 2

In [3]:
import os
from pathlib import Path

import networkx as nx
import numpy as np
import pandas as pd

from ihm_analyse import load_pickle
from ihm_analyse.lib.preprocess import merge_similarity_dupl
from ihm_analyse.lib.graphs import update_graph, get_graph_metadata


str_path = os.getcwd()
p = Path(str_path)
folder = list((p / 'results' / 'test_new2').glob('*'))
folder

[WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-3_remove_NA.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-5_analyse_feature.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-1_build_cosSim_matrix.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-2_filt_thresh_cosSim_matrix.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step_3_CosSim-FilterCandidates.xlsx'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-3_list_cosSim_dupl_candidates.pkl'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Merge_Duplicates_Step-1_merge_similarity_dupl.pkl')]

In [3]:
# dataset
res = load_pickle(folder[1])
data = res[0]
# dupl IDs
res = load_pickle(folder[-2])
dupl_ids = res[0]

INFO:ihm_analyse.helpers:Loaded file successfully.
INFO:ihm_analyse.helpers:Loaded file successfully.


In [15]:
len(dupl_ids)

9331

In [27]:
sub_ids = dupl_ids.copy()
sub_ids = dupl_ids[:20]

In [28]:
# build index graph to obtain graph of connected (similar) indices
# use this graph to obtain connected components (indices which belong together)
# retain semantic connection on whole dataset
dupl_id_graph = nx.Graph()

for (idx1, idx2) in sub_ids:
    # inplace operation, parent/child do not really exist in undirected graph
    update_graph(graph=dupl_id_graph, parent=idx1, child=idx2)

In [34]:
graph_meta = get_graph_metadata(graph=dupl_id_graph)

INFO:ihm_analyse.graphs:Graph properties: 24 Nodes, 20 Edges
INFO:ihm_analyse.graphs:Node memory: 0.66 KB
INFO:ihm_analyse.graphs:Edge memory: 1.09 KB
INFO:ihm_analyse.graphs:Total memory: 1.75 KB


In [37]:
conn_ids = nx.connected_components(dupl_id_graph)
conn_ids_tpl = tuple(conn_ids)

In [31]:
for id_set in conn_ids:
    print(id_set)

{33, 487, 5703, 176, 247, 345, 157}
{882, 131}
{561, 332, 558}
{104, 4003}
{5298, 132}
{34, 3121, 3122, 3123, 63}
{168, 6378, 1068}


In [36]:
conn_ids_lst

[{33, 157, 176, 247, 345, 487, 5703},
 {131, 882},
 {332, 558, 561},
 {104, 4003},
 {132, 5298},
 {34, 63, 3121, 3122, 3123},
 {168, 1068, 6378}]

In [33]:
data

entry  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      1654   
131               Tägliche Überprüfung der Ölabscheider   37      1616   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2678   Bitte 8 Scheiben nach Muster anfertigen.  Danke.   48         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   
6799  Befestigung Deckel für Batteriefach defekt    ...  107         1   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 331, 332, 510, 511, ...                18  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2679                                              [415]                 1  
2678                                              [140]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  
6799                                              [326]                 1  

[6800 rows x 5 columns]

In [41]:
test_ids = list(conn_ids_tpl[0])

In [114]:
sub_data = data.loc[test_ids,:].copy()

In [115]:
# obtain bunch
# filter for bunch
# merge bunch
# remove all but merged entry from whole dataset

In [116]:
sub_data = sub_data.sort_values(by=['num_occur', 'num_assoc_obj_ids', 'len'], ascending=[False, False, False])
sub_data

entry len num_occur  \
33    Wöchentliche Sichtkontrolle / Reinigung  39      1654   
157                 Monatliche Sichtkontrolle  25       634   
176     Wöchentliche Sichtprüfung / Reinigung  37       361   
247     Monatliche Sichtkontrolle / Reinigung  37       113   
487                 Wöchentliche Sichtprüfung  25        35   
345       Monatliche Sichtprüfung / Reinigung  35        33   
5703                monatliche Sichtkontrolle  25         1   

                                          assoc_obj_ids num_assoc_obj_ids  
33    [301, 304, 305, 313, 314, 331, 332, 510, 511, ...                18  
157   [1038, 1040, 1041, 1042, 1043, 1044, 1045, 121...                24  
176   [301, 304, 305, 313, 314, 323, 329, 421, 1003,...                11  
247                  [899, 906, 1052, 1169, 1170, 1725]                 6  
487                                              [1666]                 1  
345    [885, 899, 906, 945, 946, 970, 1052, 1169, 1170]                 9  
5703                                             [1725]                 1

In [117]:
# keep first entry with max number occurrences, then number of oassociated objects,
# then length of entry
data_idx = sub_data.index[0]
#entry = sub_data.iat[0,0]
#sub_data.at[data_idx, 'len'] = len(entry)
sub_data.at[data_idx, 'num_occur'] = sub_data['num_occur'].sum()
# assoc IDs
assoc_obj_ids = sub_data['assoc_obj_ids'].to_numpy()
assoc_obj_ids = np.concatenate(assoc_obj_ids)
assoc_obj_ids = np.unique(assoc_obj_ids)
sub_data.at[data_idx, 'assoc_obj_ids'] = assoc_obj_ids
sub_data.at[data_idx, 'num_assoc_obj_ids'] = len(assoc_ids_uni)

In [118]:
sub_data

entry len num_occur  \
33    Wöchentliche Sichtkontrolle / Reinigung  39      2831   
157                 Monatliche Sichtkontrolle  25       634   
176     Wöchentliche Sichtprüfung / Reinigung  37       361   
247     Monatliche Sichtkontrolle / Reinigung  37       113   
487                 Wöchentliche Sichtprüfung  25        35   
345       Monatliche Sichtprüfung / Reinigung  35        33   
5703                monatliche Sichtkontrolle  25         1   

                                          assoc_obj_ids num_assoc_obj_ids  
33    [301, 304, 305, 313, 314, 323, 329, 331, 332, ...                54  
157   [1038, 1040, 1041, 1042, 1043, 1044, 1045, 121...                24  
176   [301, 304, 305, 313, 314, 323, 329, 421, 1003,...                11  
247                  [899, 906, 1052, 1169, 1170, 1725]                 6  
487                                              [1666]                 1  
345    [885, 899, 906, 945, 946, 970, 1052, 1169, 1170]                 9  
5703                                             [1725]                 1

In [121]:
test_ids.remove(data_idx)

In [122]:
test_ids

[487, 5703, 176, 247, 345, 157]

In [123]:
sub_data2 = sub_data.drop(index=test_ids)
sub_data2

entry len num_occur  \
33  Wöchentliche Sichtkontrolle / Reinigung  39      2831   

                                        assoc_obj_ids num_assoc_obj_ids  
33  [301, 304, 305, 313, 314, 323, 329, 331, 332, ...                54

In [4]:
test_ids = dupl_ids[:5]
test_ids

[(33, 176), (33, 247), (33, 487), (131, 882), (332, 558)]

In [5]:
ret = merge_similarity_dupl_test(data=data, dupl_idx_pairs=dupl_ids)

INFO:ihm_analyse.graphs:Graph properties: 2695 Nodes, 9331 Edges
INFO:ihm_analyse.graphs:Node memory: 73.69 KB
INFO:ihm_analyse.graphs:Edge memory: 510.29 KB
INFO:ihm_analyse.graphs:Total memory: 583.98 KB


In [6]:
ret[0]

entry  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      3111   
131               Tägliche Überprüfung der Ölabscheider   37      1619   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2680  Stand 15.07.2020 (Stöppel): Herr Langner (Toyo...  260         1   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   
6799  Befestigung Deckel für Batteriefach defekt    ...  107         2   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 323, 329, 331, 332, ...                74  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2680                                              [311]                 1  
2679                                              [415]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  
6799                                         [306, 326]                 2  

[4582 rows x 5 columns]

In [7]:
data

entry  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      1654   
131               Tägliche Überprüfung der Ölabscheider   37      1616   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2678   Bitte 8 Scheiben nach Muster anfertigen.  Danke.   48         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   
6799  Befestigung Deckel für Batteriefach defekt    ...  107         1   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 331, 332, 510, 511, ...                18  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2679                                              [415]                 1  
2678                                              [140]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  
6799                                              [326]                 1  

[6800 rows x 5 columns]

## New Merge Duplicates in Pipeline

In [4]:
# dataset
res = load_pickle(folder[-1])
data = res[0]

INFO:ihm_analyse.helpers:Loaded file successfully.


In [5]:
data

entry  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      3111   
131               Tägliche Überprüfung der Ölabscheider   37      1619   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2680  Stand 15.07.2020 (Stöppel): Herr Langner (Toyo...  260         1   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   
6799  Befestigung Deckel für Batteriefach defekt    ...  107         2   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 323, 329, 331, 332, ...                74  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2680                                              [311]                 1  
2679                                              [415]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  
6799                                         [306, 326]                 2  

[4582 rows x 5 columns]